In [504]:
import pandas as pd
import numpy as np
import re
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
from sklearn.preprocessing import LabelEncoder


## Importing Libraries
import numpy as np
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense


In [505]:
df = pd.read_csv('/Users/louisgolding/Downloads/US-Economic-News.csv', delimiter=',', encoding= 'ISO-8859-1')

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8000 entries, 0 to 7999
Data columns (total 15 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   _unit_id               8000 non-null   int64  
 1   _golden                8000 non-null   bool   
 2   _unit_state            8000 non-null   object 
 3   _trusted_judgments     8000 non-null   int64  
 4   _last_judgment_at      8000 non-null   object 
 5   positivity             1420 non-null   float64
 6   positivity:confidence  3775 non-null   float64
 7   relevance              8000 non-null   object 
 8   relevance:confidence   8000 non-null   float64
 9   articleid              8000 non-null   object 
 10  date                   8000 non-null   object 
 11  headline               8000 non-null   object 
 12  positivity_gold        0 non-null      float64
 13  relevance_gold         0 non-null      float64
 14  text                   8000 non-null   object 
dtypes: b

In [506]:
df.head(5)

_unit_id  _golden _unit_state  _trusted_judgments _last_judgment_at  \
0  842613455    False   finalized                   3     12/5/15 17:48   
1  842613456    False   finalized                   3     12/5/15 16:54   
2  842613457    False   finalized                   3      12/5/15 1:59   
3  842613458    False   finalized                   3      12/5/15 2:19   
4  842613459    False   finalized                   3     12/5/15 17:48   

   positivity  positivity:confidence relevance  relevance:confidence  \
0         3.0                 0.6400       yes                 0.640   
1         NaN                    NaN        no                 1.000   
2         NaN                    NaN        no                 1.000   
3         NaN                 0.0000        no                 0.675   
4         3.0                 0.3257       yes                 0.640   

       articleid      date                                           headline  \
0  wsj_398217788   8/14/91              Yields on CDs Fell in the Latest Week   
1  wsj_399019502   8/21/07  The Morning Brief: White House Seeks to Limit ...   
2  wsj_398284048  11/14/91  Banking Bill Negotiators Set Compromise --- Pl...   
3  wsj_397959018   6/16/86  Manager's Journal: Sniffing Out Drug Abusers I...   
4  wsj_398838054   10/4/02  Currency Trading: Dollar Remains in Tight Rang...   

   positivity_gold  relevance_gold  \
0              NaN             NaN   
1              NaN             NaN   
2              NaN             NaN   
3              NaN             NaN   
4              NaN             NaN   

                                                text  
0  NEW YORK -- Yields on most certificates of dep...  
1  The Wall Street Journal Online</br></br>The Mo...  
2  WASHINGTON -- In an effort to achieve banking ...  
3  The statistics on the enormous costs of employ...  
4  NEW YORK -- Indecision marked the dollar's ton...

In [507]:
df = df[['headline', 'text', 'relevance']]

# We drop all irrelavant features to only keep headline and text for 2 reasons: 
# The other features seem either irrelevant or we lack documentation
# With headline and text only, our final model will be more generalizable. We could in theory apply it to any article.

In [508]:
df.head()

headline  \
0              Yields on CDs Fell in the Latest Week   
1  The Morning Brief: White House Seeks to Limit ...   
2  Banking Bill Negotiators Set Compromise --- Pl...   
3  Manager's Journal: Sniffing Out Drug Abusers I...   
4  Currency Trading: Dollar Remains in Tight Rang...   

                                                text relevance  
0  NEW YORK -- Yields on most certificates of dep...       yes  
1  The Wall Street Journal Online</br></br>The Mo...        no  
2  WASHINGTON -- In an effort to achieve banking ...        no  
3  The statistics on the enormous costs of employ...        no  
4  NEW YORK -- Indecision marked the dollar's ton...       yes

In [509]:
#pip install nltk

In [510]:
# #Ensure you have downloaded the necessary NLTK data
#nltk.download('punkt')
#nltk.download('stopwords')
#nltk.download('wordnet')

In [511]:
df['whole_txt'] = df['headline']+ ' ' + df['text']
wtxt_train = np.array(df['whole_txt'])


In [512]:
# print(wtxt_train)

In [513]:
for i in range(len(wtxt_train)):
    # Deletion of non-latin alfabet signs, also numbers
    wtxt_train[i] = re.sub(r'[^a-zA-Z]', ' ', wtxt_train[i])
    # Removing single letter works like 'a'.
    wtxt_train[i] = re.sub(r"\s+[a-zA-Z]\s+", ' ', wtxt_train[i])
    # Removing double spaces
    wtxt_train[i] = re.sub(r'\s+', ' ', wtxt_train[i])
    # Lower case
    wtxt_train[i] = wtxt_train[i].lower()

## Tokenization

In [514]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences

# Taking out '<br>' in the 'whole_text' column
df['whole_txt'] = df['whole_txt'].str.replace(r'</?br>', '', regex=True)

print(df['whole_txt'].iloc[0])

sentences = df['whole_txt'].apply(lambda text: sent_tokenize(text))

tokenizer = Tokenizer()
tokenizer.fit_on_texts(sentences)



Yields on CDs Fell in the Latest Week NEW YORK -- Yields on most certificates of deposit offered by major banks dropped more than a tenth of a percentage point in the latest week, reflecting the overall decline in short-term interest rates.On small-denomination, or "consumer," CDs sold directly by banks, the average yield on six-month deposits fell to 5.49% from 5.62% in the week ended yesterday, according to an 18-bank survey by Banxquote Money Markets, a Wilmington, Del., information service.On three-month "consumer" deposits, the average yield sank to 5.29% from 5.42% the week before, according to Banxquote. Two banks in the Banxquote survey, Citibank in New York and CoreStates in Pennsylvania, are paying less than 5% on threemonth small-denomination CDs.Declines were somewhat smaller on five-year consumer CDs, which eased to 7.37% from 7.45%, Banxquote said.Yields on three-month and six-month Treasury bills sold at Monday's auction plummeted more than a fifth of a percentage point 

In [515]:
sequences = tokenizer.texts_to_sequences(sentences)
sequences

[[293, 294],
 [295, 296, 297, 298, 299, 300, 301, 302, 303],
 [304, 305, 306],
 [307,
  308,
  309,
  310,
  311,
  312,
  313,
  314,
  315,
  316,
  317,
  318,
  319,
  320,
  321,
  322,
  323],
 [324, 325, 326],
 [327, 328],
 [329, 330, 331, 332, 333, 334],
 [335,
  336,
  337,
  338,
  339,
  340,
  341,
  342,
  343,
  344,
  345,
  346,
  347,
  348,
  349,
  350,
  351,
  352,
  353],
 [354, 355, 356, 357, 358],
 [359, 360, 361, 362, 363, 364],
 [365, 366, 367, 368, 369, 370],
 [371, 372, 373, 374, 375],
 [376, 377, 378, 379, 380, 381, 382],
 [383, 384, 385, 386, 387, 388],
 [389, 390, 1, 391],
 [392, 393, 394, 395, 396, 397, 398, 399, 400, 401, 402, 403],
 [404, 405, 406, 407, 408, 409, 410, 411, 412, 413, 414, 415],
 [416, 417, 418, 419],
 [420, 421, 422, 423, 424, 425, 426, 427],
 [428, 429, 430, 431],
 [432, 433, 434, 435, 436, 437, 438, 439],
 [440, 441, 442, 443, 444, 445],
 [446, 447, 448, 449, 450, 451, 452, 453],
 [454],
 [455, 456, 457],
 [458, 459, 460, 461, 462],
 

In [516]:
padded_sequences = pad_sequences(sequences)
padded_sequences

array([[    0,     0,     0, ...,     0,   293,   294],
       [    0,     0,     0, ...,   301,   302,   303],
       [    0,     0,     0, ...,   304,   305,   306],
       ...,
       [    0,     0,     0, ..., 55174, 55175, 55176],
       [    0,     0,     0, ..., 55184, 55185, 55186],
       [    0,     0,     0, ..., 55188, 55189, 55190]], dtype=int32)

In [517]:
# We check that the arrays are the same size in order to make sure the padding was done effectively. 

sequence_lengths = [len(sequence) for sequence in padded_sequences]
unique_lengths = set(sequence_lengths)

print(unique_lengths)

{44}


In [518]:
# We remove unecessary columns and add padded column. 
df = df.drop(['headline', 'text'], axis=1)
df['padded_sequences'] = list(padded_sequences)

In [519]:
df.head(5)

relevance                                          whole_txt  \
0       yes  Yields on CDs Fell in the Latest Week NEW YORK...   
1        no  The Morning Brief: White House Seeks to Limit ...   
2        no  Banking Bill Negotiators Set Compromise --- Pl...   
3        no  Manager's Journal: Sniffing Out Drug Abusers I...   
4       yes  Currency Trading: Dollar Remains in Tight Rang...   

                                    padded_sequences  
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
2  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
4  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...

## Model building

In [520]:
embedding_dim = 10

total_words = len(tokenizer.word_index) + 1

input_length = len(padded_sequences[0])

# We are going to build our model with the Sequential API
model = Sequential()
model.add(Embedding(total_words,      # number of words to process as input
                    embedding_dim,    # output representation
                    input_length=len(padded_sequences[0])))    # total length of each observation
model.add(LSTM(100, return_sequences=False))
model.add(Dense(3, activation='sigmoid'))  # Change activation based on the number of classes

model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

In [521]:
model(padded_sequences)

<tf.Tensor: shape=(8000, 3), dtype=float32, numpy=
array([[0.5003454 , 0.4994834 , 0.4989731 ],
       [0.4998406 , 0.49990165, 0.4999769 ],
       [0.49968332, 0.5001589 , 0.5003817 ],
       ...,
       [0.4998215 , 0.4986824 , 0.4991676 ],
       [0.5001528 , 0.49978086, 0.49964824],
       [0.50054294, 0.5008399 , 0.50099117]], dtype=float32)>

## Training model

In [522]:
labels = df['relevance']


# Convert string labels to numerical format
label_encoder = LabelEncoder()
labels_encoded = label_encoder.fit_transform(labels)


labels_one_hot = to_categorical(labels_encoded)

X_train, X_test, y_train, y_test = train_test_split(padded_sequences, labels_one_hot, test_size=0.2, random_state=42)

model.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_test, y_test))



Epoch 1/10
200/200 [==============================] - 5s 20ms/step - loss: 0.5135 - accuracy: 0.8206 - val_loss: 0.4879 - val_accuracy: 0.8144
Epoch 2/10
200/200 [==============================] - 4s 19ms/step - loss: 0.4680 - accuracy: 0.8231 - val_loss: 0.4851 - val_accuracy: 0.8144
Epoch 3/10
200/200 [==============================] - 4s 19ms/step - loss: 0.1905 - accuracy: 0.9281 - val_loss: 0.6790 - val_accuracy: 0.8075
Epoch 4/10
200/200 [==============================] - 4s 19ms/step - loss: 0.0196 - accuracy: 0.9956 - val_loss: 0.9275 - val_accuracy: 0.4675
Epoch 5/10
200/200 [==============================] - 4s 18ms/step - loss: 0.0124 - accuracy: 0.9975 - val_loss: 0.6684 - val_accuracy: 0.7200
Epoch 6/10
200/200 [==============================] - 4s 19ms/step - loss: 0.0099 - accuracy: 0.9983 - val_loss: 1.0363 - val_accuracy: 0.4800
Epoch 7/10
200/200 [==============================] - 4s 19ms/step - loss: 0.0082 - accuracy: 0.9986 - val_loss: 0.9080 - val_accuracy: 0.5600

### Removing stop words

In [337]:
stop_words = set(stopwords.words('english'))

for i in range(len(wtxt_train)):
    wtxt_train[i] = [word for word in wtxt_train[i] if word not in stop_words]

In [338]:
stop_words = set(stopwords.words('english'))

for i in range(len(wtxt_train)):
    wtxt_train[i] = [word for word in wtxt_train[i] if word not in stop_words]

In [339]:
wtxt_train[0]
# stop_words

['yields',
 'cds',
 'fell',
 'latest',
 'week',
 'new',
 'york',
 'yields',
 'certificates',
 'deposit',
 'offered',
 'major',
 'banks',
 'dropped',
 'tenth',
 'percentage',
 'point',
 'latest',
 'week',
 'reflecting',
 'overall',
 'decline',
 'short',
 'term',
 'interest',
 'rates',
 'br',
 'br',
 'small',
 'denomination',
 'consumer',
 'cds',
 'sold',
 'directly',
 'banks',
 'average',
 'yield',
 'six',
 'month',
 'deposits',
 'fell',
 'week',
 'ended',
 'yesterday',
 'according',
 'bank',
 'survey',
 'banxquote',
 'money',
 'markets',
 'wilmington',
 'del',
 'information',
 'service',
 'br',
 'br',
 'three',
 'month',
 'consumer',
 'deposits',
 'average',
 'yield',
 'sank',
 'week',
 'according',
 'banxquote',
 'two',
 'banks',
 'banxquote',
 'survey',
 'citibank',
 'new',
 'york',
 'corestates',
 'pennsylvania',
 'paying',
 'less',
 'threemonth',
 'small',
 'denomination',
 'cds',
 'br',
 'br',
 'declines',
 'somewhat',
 'smaller',
 'five',
 'year',
 'consumer',
 'cds',
 'eased',
 

In [340]:
df.head()

headline  \
0              Yields on CDs Fell in the Latest Week   
1  The Morning Brief: White House Seeks to Limit ...   
2  Banking Bill Negotiators Set Compromise --- Pl...   
3  Manager's Journal: Sniffing Out Drug Abusers I...   
4  Currency Trading: Dollar Remains in Tight Rang...   

                                                text relevance  \
0  NEW YORK -- Yields on most certificates of dep...       yes   
1  The Wall Street Journal Online</br></br>The Mo...        no   
2  WASHINGTON -- In an effort to achieve banking ...        no   
3  The statistics on the enormous costs of employ...        no   
4  NEW YORK -- Indecision marked the dollar's ton...       yes   

                                           whole_txt  
0  Yields on CDs Fell in the Latest Week NEW YORK...  
1  The Morning Brief: White House Seeks to Limit ...  
2  Banking Bill Negotiators Set Compromise --- Pl...  
3  Manager's Journal: Sniffing Out Drug Abusers I...  
4  Currency Trading: Dollar Remains in Tight Rang...

In [341]:
df['whole_txt'].iloc[0]

'Yields on CDs Fell in the Latest Week NEW YORK -- Yields on most certificates of deposit offered by major banks dropped more than a tenth of a percentage point in the latest week, reflecting the overall decline in short-term interest rates.</br></br>On small-denomination, or "consumer," CDs sold directly by banks, the average yield on six-month deposits fell to 5.49% from 5.62% in the week ended yesterday, according to an 18-bank survey by Banxquote Money Markets, a Wilmington, Del., information service.</br></br>On three-month "consumer" deposits, the average yield sank to 5.29% from 5.42% the week before, according to Banxquote. Two banks in the Banxquote survey, Citibank in New York and CoreStates in Pennsylvania, are paying less than 5% on threemonth small-denomination CDs.</br></br>Declines were somewhat smaller on five-year consumer CDs, which eased to 7.37% from 7.45%, Banxquote said.</br></br>Yields on three-month and six-month Treasury bills sold at Monday\'s auction plummete

In [342]:
# Taking out '<br>' in the 'whole_text' column
df['whole_txt'] = df['whole_txt'].str.replace(r'</?br>', ' ', regex=True)

print(df['whole_txt'].iloc[0])

Yields on CDs Fell in the Latest Week NEW YORK -- Yields on most certificates of deposit offered by major banks dropped more than a tenth of a percentage point in the latest week, reflecting the overall decline in short-term interest rates.  On small-denomination, or "consumer," CDs sold directly by banks, the average yield on six-month deposits fell to 5.49% from 5.62% in the week ended yesterday, according to an 18-bank survey by Banxquote Money Markets, a Wilmington, Del., information service.  On three-month "consumer" deposits, the average yield sank to 5.29% from 5.42% the week before, according to Banxquote. Two banks in the Banxquote survey, Citibank in New York and CoreStates in Pennsylvania, are paying less than 5% on threemonth small-denomination CDs.  Declines were somewhat smaller on five-year consumer CDs, which eased to 7.37% from 7.45%, Banxquote said.  Yields on three-month and six-month Treasury bills sold at Monday's auction plummeted more than a fifth of a percentag

In [343]:
text_content = df['whole_txt'].iloc[0]

sentences = sent_tokenize(text_content)

# Calculate the length (number of words) for each sentence
sentence_lengths = [len(word_tokenize(sentence)) for sentence in sentences]

for i, length in enumerate(sentence_lengths, 1):
    print(f"Length of sentence {i}: {length} words")



Length of sentence 1: 44 words
Length of sentence 2: 51 words
Length of sentence 3: 25 words
Length of sentence 4: 27 words
Length of sentence 5: 21 words
Length of sentence 6: 35 words


## Lemmatization

In [344]:
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import sent_tokenize, word_tokenize

# Create a lemmatizer instance
lemmatizer = WordNetLemmatizer()

# Assuming 'whole_txt' is the column containing text with multiple sentences
df['whole_txt'] = df['whole_txt'].apply(lambda text: ' '.join([lemmatizer.lemmatize(word) for word in word_tokenize(text)]))

# Drop unnecessary columns
df = df.drop(['headline', 'text'], axis=1)

# Display the DataFrame
df.head(5)



relevance                                          whole_txt
0       yes  Yields on CDs Fell in the Latest Week NEW YORK...
1        no  The Morning Brief : White House Seeks to Limit...
2        no  Banking Bill Negotiators Set Compromise -- - P...
3        no  Manager 's Journal : Sniffing Out Drug Abusers...
4       yes  Currency Trading : Dollar Remains in Tight Ran...

In [345]:
text_content = df['whole_txt'].iloc[0]

sentences = df['whole_txt'].apply(lambda text: sent_tokenize(text))
tokenizer = Tokenizer()
tokenizer.fit_on_texts(sentences)

# Calculate the length (number of words) for each sentence
sentence_lengths = [len(word_tokenize(sentence)) for sentence in sentences]

for i, length in enumerate(sentence_lengths, 1):
    print(f"Length of sentence {i}: {length} words")



Length of sentence 1: 44 words
Length of sentence 2: 48 words
Length of sentence 3: 4 words
Length of sentence 4: 25 words
Length of sentence 5: 27 words
Length of sentence 6: 21 words
Length of sentence 7: 35 words


In [346]:
sequences = tokenizer.texts_to_sequences(df['whole_txt'])
padded_sequences = pad_sequences(sequences)

In [347]:
sequences

[[629,
  11,
  4457,
  144,
  6,
  1,
  445,
  83,
  29,
  73,
  629,
  11,
  84,
  8064,
  3,
  1664,
  1057,
  14,
  214,
  103,
  460,
  31,
  37,
  5,
  5423,
  3,
  5,
  454,
  175,
  6,
  1,
  445,
  83,
  1821,
  1,
  604,
  225,
  6,
  231,
  165,
  54,
  53,
  11,
  292,
  16787,
  36,
  187,
  9901,
  4457,
  686,
  2037,
  14,
  103,
  1,
  94,
  472,
  11,
  382,
  118,
  1664,
  144,
  4,
  67,
  1547,
  18,
  67,
  1449,
  6,
  1,
  83,
  405,
  93,
  189,
  4,
  27,
  503,
  103,
  542,
  14,
  12880,
  107,
  131,
  5,
  9344,
  3808,
  761,
  452,
  11,
  150,
  118,
  187,
  9901,
  1664,
  1,
  94,
  472,
  2342,
  4,
  67,
  869,
  18,
  67,
  1305,
  1,
  83,
  164,
  189,
  4,
  12880,
  87,
  103,
  6,
  1,
  12880,
  542,
  5278,
  6,
  29,
  73,
  7,
  10742,
  6,
  3071,
  20,
  1068,
  9892,
  37,
  67,
  11,
  26815,
  292,
  16787,
  4457,
  642,
  51,
  1484,
  989,
  11,
  327,
  22,
  187,
  4457,
  43,
  1811,
  4,
  120,
  1098,
  18,
  120,
  929,
  1

In [301]:
padded_sequences

array([[   0,    0,    0, ...,   67, 1631, 3041],
       [   0,    0,    0, ...,    7,  209,  274],
       [   0,    0,    0, ...,    1,  490,  129],
       ...,
       [   0,    0,    0, ...,    4,  660,  188],
       [   0,    0,    0, ...,  212,   40,  202],
       [   0,    0,    0, ...,  133, 1600,   63]], dtype=int32)

In [294]:
from sklearn.model_selection import train_test_split
X = df.drop(columns=['relevance'], axis = 1)
y = df['relevance']

# here stratify is used to balance dataset as much as possible
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)


In [295]:
X_train.head(3)

whole_txt
420   Trade Deficit Worry Nearly Halts Activity In E...
3350  Tea-Party Activists Complicate Republican Come...
6716  The Elder Share ONE OF the great feat of socia...

In [296]:
y_train.head(3)

420      no
3350     no
6716    yes
Name: relevance, dtype: object

In [297]:
word_index

{'the': 1,
 'br': 2,
 'of': 3,
 'to': 4,
 'a': 5,
 'in': 6,
 'and': 7,
 'that': 8,
 'for': 9,
 'is': 10,
 'on': 11,
 'as': 12,
 'at': 13,
 'by': 14,
 'it': 15,
 'said': 16,
 'with': 17,
 'from': 18,
 'was': 19,
 'are': 20,
 'but': 21,
 'year': 22,
 'have': 23,
 'be': 24,
 'has': 25,
 'its': 26,
 'an': 27,
 'market': 28,
 'new': 29,
 'this': 30,
 'more': 31,
 's': 32,
 'will': 33,
 '1': 34,
 'u': 35,
 'or': 36,
 'than': 37,
 'stock': 38,
 'he': 39,
 'their': 40,
 'up': 41,
 'they': 42,
 'which': 43,
 'about': 44,
 'would': 45,
 'rates': 46,
 'percent': 47,
 'federal': 48,
 'economic': 49,
 'not': 50,
 'were': 51,
 'last': 52,
 'rate': 53,
 'interest': 54,
 'some': 55,
 'economy': 56,
 'prices': 57,
 '2': 58,
 'billion': 59,
 'been': 60,
 'one': 61,
 'inflation': 62,
 'million': 63,
 'his': 64,
 'had': 65,
 'after': 66,
 '5': 67,
 'other': 68,
 'when': 69,
 '3': 70,
 'who': 71,
 'first': 72,
 'york': 73,
 'years': 74,
 'investors': 75,
 'over': 76,
 '4': 77,
 'out': 78,
 'if': 79,
 'grow

In [298]:
total_words

50754

In [140]:
df.head()

headline  \
0              Yields on CDs Fell in the Latest Week   
1  The Morning Brief: White House Seeks to Limit ...   
2  Banking Bill Negotiators Set Compromise --- Pl...   
3  Manager's Journal: Sniffing Out Drug Abusers I...   
4  Currency Trading: Dollar Remains in Tight Rang...   

                                                text relevance  \
0  NEW YORK -- Yields on most certificates of dep...       yes   
1  The Wall Street Journal Online</br></br>The Mo...        no   
2  WASHINGTON -- In an effort to achieve banking ...        no   
3  The statistics on the enormous costs of employ...        no   
4  NEW YORK -- Indecision marked the dollar's ton...       yes   

                                           whole_txt  
0  Yields on CDs Fell in the Latest Week NEW YORK...  
1  The Morning Brief: White House Seeks to Limit ...  
2  Banking Bill Negotiators Set Compromise --- Pl...  
3  Manager's Journal: Sniffing Out Drug Abusers I...  
4  Currency Trading: Dollar Remains in Tight Rang...

In [141]:
sequences = tokenizer.texts_to_sequences(df['text'])
padded_sequences = pad_sequences(sequences)

In [142]:
sequences ## We can see 29 is 'new', we verifiy this looking at word_index

[[29,
  73,
  629,
  11,
  84,
  3553,
  3,
  1664,
  1057,
  14,
  214,
  155,
  460,
  31,
  37,
  5,
  5423,
  3,
  5,
  454,
  175,
  6,
  1,
  445,
  83,
  1821,
  1,
  604,
  225,
  6,
  231,
  165,
  54,
  46,
  2,
  2,
  11,
  292,
  16787,
  36,
  187,
  4457,
  686,
  2037,
  14,
  155,
  1,
  94,
  472,
  11,
  382,
  118,
  1657,
  144,
  4,
  67,
  1547,
  18,
  67,
  1449,
  6,
  1,
  83,
  405,
  93,
  189,
  4,
  27,
  503,
  103,
  542,
  14,
  12880,
  107,
  131,
  5,
  9344,
  3808,
  761,
  452,
  2,
  2,
  11,
  150,
  118,
  187,
  1657,
  1,
  94,
  472,
  2342,
  4,
  67,
  869,
  18,
  67,
  1305,
  1,
  83,
  164,
  189,
  4,
  12880,
  87,
  155,
  6,
  1,
  12880,
  542,
  5278,
  6,
  29,
  73,
  7,
  10742,
  6,
  3071,
  20,
  1068,
  208,
  37,
  67,
  11,
  26815,
  292,
  16787,
  4457,
  2,
  2,
  642,
  51,
  1484,
  989,
  11,
  327,
  22,
  187,
  4457,
  43,
  1811,
  4,
  120,
  1098,
  18,
  120,
  929,
  12880,
  16,
  2,
  2,
  629,
  11,
  1

In [75]:
padded_sequences

array([[   0,    0,    0, ...,   67, 1631, 3041],
       [   0,    0,    0, ...,    7,  209, 7992],
       [   0,    0,    0, ...,    1,  223,  129],
       ...,
       [   0,    0,    0, ...,    4,  660,  188],
       [   0,    0,    0, ...,  212,   40,  415],
       [   0,    0,    0, ...,  133, 1600,   63]], dtype=int32)